In [1]:
model_name_or_path = "abdulhade/whisper-large-v2-ckb"
task = "transcribe"

In [2]:
dataset_name = "razhan/asosoft-speech"
language = "english"
language_abbr = "ckb" # Short hand code for the language we want to fine-tune

In [3]:
!pip install -q datasets
!pip install evaluate>=0.30

In [4]:
!pip install accelerate

In [5]:
!pip install jiwer

In [6]:
!pip install -q pytube
!pip install evaluate>=0.30
!pip install -q librosa
!pip install  soundfile
!pip install -q transformers
!pip install -q torch
!pip install  -q pydub

In [7]:
from huggingface_hub import notebook_login

notebook_login()

In [8]:
from datasets import load_dataset, DatasetDict

#common_voice = DatasetDict()
common_voice= load_dataset(dataset_name, split="test", use_auth_token=True)
#common_voice= load_dataset(dataset_name, language_abbr, split="test", use_auth_token=True)

/usr/local/lib/python3.10/dist-packages/datasets/load.py:2089: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=True' instead.
  warnings.warn(


In [9]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v2", language="persian")
tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-large-v2", language="persian", task="transcribe")
Processor = WhisperProcessor.from_pretrained("openai/whisper-large-v2", language="persian", task="transcribe")

In [10]:
processor=Processor

In [11]:
from datasets import Audio

common_voice = common_voice.cast_column("audio", Audio(sampling_rate=16000))

In [12]:
common_voice

Dataset({
    features: ['audio', 'transcription', 'duration'],
    num_rows: 600
})

In [13]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids

    batch["labels"] = tokenizer(batch["transcription"]).input_ids
    return batch

In [14]:
common_voice = common_voice.map(prepare_dataset, remove_columns=common_voice.column_names, num_proc=2)

In [15]:
common_voice

Dataset({
    features: ['input_features', 'labels'],
    num_rows: 600
})

In [16]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union


@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [17]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=Processor)

In [18]:
import evaluate

metric = evaluate.load("wer")

In [19]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [20]:

from transformers import WhisperForConditionalGeneration, Seq2SeqTrainer

model_id = "abdulhade/whisper-large-v2-ckb" # Use the same model ID as before.

model = WhisperForConditionalGeneration.from_pretrained(model_id,device_map="auto", torch_dtype=torch.float16)

model.config.use_cache = True

In [21]:
import gc
import numpy as np
from tqdm import tqdm
from torch.utils.data import DataLoader
from transformers.models.whisper.english_normalizer import BasicTextNormalizer

eval_dataloader = DataLoader(common_voice, batch_size=1, collate_fn=data_collator)
forced_decoder_ids = processor.get_decoder_prompt_ids(language=language, task=task)
normalizer = BasicTextNormalizer()

predictions = []
references = []
normalized_predictions = []
normalized_references = []

model.eval()
for step, batch in enumerate(tqdm(eval_dataloader)):
    with torch.cuda.amp.autocast():
        with torch.no_grad():
            generated_tokens = (
                model.generate(
                    input_features=batch["input_features"].to("cuda"),
                    forced_decoder_ids=forced_decoder_ids,
                    max_new_tokens=255,
                )
                .cpu()
                .numpy()
            )
            labels = batch["labels"].cpu().numpy()
            labels = np.where(labels != -100, labels, processor.tokenizer.pad_token_id)
            decoded_preds = processor.tokenizer.batch_decode(generated_tokens, skip_special_tokens=True)
            decoded_labels = processor.tokenizer.batch_decode(labels, skip_special_tokens=True)
            print(decoded_preds)
            print(decoded_labels)
            predictions.extend(decoded_preds)
            references.extend(decoded_labels)
            normalized_predictions.extend([normalizer(pred).strip() for pred in decoded_preds])
            normalized_references.extend([normalizer(label).strip() for label in decoded_labels])
        del generated_tokens, labels, batch
    gc.collect()
wer = 100 * metric.compute(predictions=predictions, references=references)
normalized_wer = 100 * metric.compute(predictions=normalized_predictions, references=normalized_references)
eval_metrics = {"eval/wer": wer, "eval/normalized_wer": normalized_wer}

print(f"{wer=} and {normalized_wer=}")
print(eval_metrics)

  0%|          | 1/600 [00:10<1:44:01, 10.42s/it]

['پاش موسوڵمان بوونی بڕیاری دا بەرگی باڵاپۆشیش لە بەر بکات']
['پاش موسڵمان بوونی بڕیاری دا بەرگی باڵاپۆشیش لە بەر بکات.']


  0%|          | 2/600 [00:13<58:52,  5.91s/it]  

['ئافرەتانی کورد بۆ لەفرەژنی دەترسن']
['ئافرەتانی کورد بۆ لە فرەژنی دەترسن.']
['داوای بەخشیش و یارمەتی لە خودا بکەن']
['داوای بەخشش و یارمەتی لە خودا بکەن.']


  0%|          | 3/600 [00:15<40:16,  4.05s/it]

...

['سەرەتا باسی ژیاننامەی خۆت بکە و سەرەتای منداڵی چۆن تێپەڕاند']
['سەرەتا باسی ژیاننامەی خۆت بکە و سەرەتای منداڵیت چۆن تێپەڕاند.']


100%|█████████▉| 599/600 [30:53<00:03,  3.47s/it]

['وەک خانمە نووسەر و ڕووناکبیرێکی کورد چۆن لە چالاکی ئەو ژنانە دەڕوانیت کە دێنە مەیدانی نووسین']
['وەک خانمە نووسەر و ڕووناکبیرێکی کورد چۆن لە چالاکیی ئەو ژنانە دەڕوانیت کە دێنە مەیدانی نووسین؟']


100%|██████████| 600/600 [30:55<00:00,  3.09s/it]

['پرۆژەیەکی تایبەتت بۆ کاروچالاکییەکانی دواترت هەیە']
['پڕۆژەیەکی تایبەتت بۆ کار و چالاکییەکانی دواترت هەیە؟']
wer=25.3495217071376 and normalized_wer=14.992641648270787
{'eval/wer': 25.3495217071376, 'eval/normalized_wer': 14.992641648270787}


In [22]:
normalized_references

['پاش موسڵمان بوونی بڕیاری دا بەرگی باڵاپۆشیش لە بەر بکات',
 'ئافرەتانی کورد بۆ لە فرەژنی دەترسن',
 'داوای بەخشش و یارمەتی لە خودا بکەن',
 'خوای گەورە بانگت دەکات بۆ پەیوەست بوونت بە فەرمانەکانی',
 'پێغەمبەری سەروەر ناوی چاکی لا پەسند بوو',
 'هاوەڵ بۆ خودا پەیداکردن ستەمێکى گەورەیە',
 'مەسەلەى عەقیدە ڕاستەوخۆ پەیوەستە بە قورئان و سوننەتەوە',
 'زانا و گەورە ڕووناکبیری ئیسلامی کۆچی دوایی کرد',
 'بە پشتیوانیی خوا هەڵدەستین بە سازدانی کۆڕێکی ئیمانی',
 'هەموو ئەمانە ئەسڵ و بنەمایەکیان نییە لە شەرعدا',
 'یانەى هەولێر سورپرایزی بۆ هاندەرانی هەیە',
 'ڕۆناڵدۆ بەڵێنی دابوو ئەگەر گۆڵ بکات بە هاندەران بڵێت بێدەنگ بن',
 'ناوى یانە بەشدارەکانى جامى جیهانیی یانەکان ئاشکرا کران',
 'یاریزانێکی هەڵبژاردەی عێراق ماڵئاوایی لە ژیان کرد',
 'ئەوە گەورەترین مووچەیە کە لە مێژوودا یاریزانێک وەری گرتبێت',
 'یانەی ڕیال بە سەرکەوتن لە پلەی یەکەمی خولەکەدا وەستا',
 'درگای گواستنەوەی ئەو یاریزانە بە ڕووی هەموو یانەکاندا داخرا',
 'لیستی ڕەشی ڕاهێنەرەکەی دایە بەرپرسانی یانەی شەیتانە سوورەکە',
 'پەنجا کەس لە جەمسەری با

In [23]:
normalized_predictions

['پاش موسوڵمان بوونی بڕیاری دا بەرگی باڵاپۆشیش لە بەر بکات',
 'ئافرەتانی کورد بۆ لەفرەژنی دەترسن',
 'داوای بەخشیش و یارمەتی لە خودا بکەن',
 'خوای گەورە بانگت دەکات بۆ پەیوەستبوونت بە فەرمانەکانی',
 'پێغەمبەری سەروەر ناوی چاکی لاپەسند بوو',
 'هەوڵ بۆ خودا پەیدا کردن ستەمێکی گەورەیە',
 'مەسەلەی عەقیدە ڕاستەوخۆ پەیوەستە بە قورئان و سوننەتەوە',
 'زانا و گەورە ڕووناکبیری ئیسلامی کۆچی دوایی کرد',
 'بە پشتیوانی خوا هەڵدەستێن بە سازدانی کۆڕێکی ئیمانی',
 'هەموو ئەمانە ئەسڵ و بنەمایەکیان نییە لە شەرعدا',
 'یانەی هەولێر سوپرایزی بۆ هاندەرانی هەیە',
 'ڕۆناڵدۆ بەڵێنی دابوو ئەگەر گوڵ بکات بە هاندەرانی بڵێن بێدەنگ بن',
 'ناوی یانە بەشدارەکانی جامی جیهانی یانەکان ئاشکرا کرا',
 'یاریزانێکی هەڵبژاردەی عێراق ماڵاوایی لە ژیان کرد',
 'ئەوە گەورەترین مووچەیەکە لە مێژوودا یاریزانێک وەریگرتبێت',
 'یانەی ڕیال بە سەرکەوتن لە پلەی یەکەمی خولەکەدا وەستا',
 'دەرگای گواستنەوەی ئەو یاریزانە بە ڕووی هەموو یانەکاندا داخرا',
 'لیستی ڕەشی ڕاهێنەرەکەی دایە بەر پرسانی یانە شەیتانە سوورەکە',
 'پەنجا کەس لە جەمسەری باشوور م